In [0]:
from time import time
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.decomposition import NMF, LatentDirichletAllocation
from sklearn.datasets import fetch_20newsgroups


In [0]:
n_samples = 2000
n_features = 1000
n_components = 10
n_top_words = 20


In [0]:
def print_top_words(model, feature_names, n_top_words):
    for topic_idx, topic in enumerate(model.components_):
        message = "Topic #%d: " % topic_idx
        message += " ".join([feature_names[i]
                             for i in topic.argsort()[:-n_top_words - 1:-1]])
        print(message)
    print()

In [10]:
print("Loading dataset...")
t0 = time()
data, _ = fetch_20newsgroups(shuffle=True, random_state=1,
                             remove=('headers', 'footers', 'quotes'),
                             return_X_y=True)
data_samples = data[:n_samples]
print("done in %0.3fs." % (time() - t0))

Loading dataset...
done in 11.565s.


In [11]:
print("Extracting tf-idf features for NMF...")
tfidf_vectorizer = TfidfVectorizer(max_df=0.95, min_df=2,
                                   max_features=n_features,
                                   stop_words='english')

Extracting tf-idf features for NMF...


In [12]:
t0 = time()
tfidf = tfidf_vectorizer.fit_transform(data_samples)
print("done in %0.3fs." % (time() - t0))

# Use tf (raw term count) features for LDA.
print("Extracting tf features for LDA...")
tf_vectorizer = CountVectorizer(max_df=0.95, min_df=2,
                                max_features=n_features,
                                stop_words='english')
t0 = time()
tf = tf_vectorizer.fit_transform(data_samples)
print("done in %0.3fs." % (time() - t0))
print()

done in 0.350s.
Extracting tf features for LDA...
done in 0.340s.



In [13]:
print("Fitting the NMF model (Frobenius norm) with tf-idf features, "
      "n_samples=%d and n_features=%d..."
      % (n_samples, n_features))
t0 = time()
nmf = NMF(n_components=n_components, random_state=1,
          alpha=.1, l1_ratio=.5).fit(tfidf)
print("done in %0.3fs." % (time() - t0))

print("\nTopics in NMF model (Frobenius norm):")
tfidf_feature_names = tfidf_vectorizer.get_feature_names()
print_top_words(nmf, tfidf_feature_names, n_top_words)

# Fit the NMF model
print("Fitting the NMF model (generalized Kullback-Leibler divergence) with "
      "tf-idf features, n_samples=%d and n_features=%d..."
      % (n_samples, n_features))
t0 = time()
nmf = NMF(n_components=n_components, random_state=1,
          beta_loss='kullback-leibler', solver='mu', max_iter=1000, alpha=.1,
          l1_ratio=.5).fit(tfidf)
print("done in %0.3fs." % (time() - t0))

print("\nTopics in NMF model (generalized Kullback-Leibler divergence):")
tfidf_feature_names = tfidf_vectorizer.get_feature_names()
print_top_words(nmf, tfidf_feature_names, n_top_words)

print("Fitting LDA models with tf features, "
      "n_samples=%d and n_features=%d..."
      % (n_samples, n_features))
lda = LatentDirichletAllocation(n_components=n_components, max_iter=5,
                                learning_method='online',
                                learning_offset=50.,
                                random_state=0)
t0 = time()
lda.fit(tf)
print("done in %0.3fs." % (time() - t0))

print("\nTopics in LDA model:")
tf_feature_names = tf_vectorizer.get_feature_names()
print_top_words(lda, tf_feature_names, n_top_words)

Fitting the NMF model (Frobenius norm) with tf-idf features, n_samples=2000 and n_features=1000...
done in 0.389s.

Topics in NMF model (Frobenius norm):
Topic #0: just people don think like know time good make way really say right ve want did ll new use years
Topic #1: windows use dos using window program os drivers application help software pc running ms screen files version card code work
Topic #2: god jesus bible faith christian christ christians does heaven sin believe lord life church mary atheism belief human love religion
Topic #3: thanks know does mail advance hi info interested email anybody looking card help like appreciated information send list video need
Topic #4: car cars tires miles 00 new engine insurance price condition oil power speed good 000 brake year models used bought
Topic #5: edu soon com send university internet mit ftp mail cc pub article information hope program mac email home contact blood
Topic #6: file problem files format win sound ftp pub read save sit

In [0]:
def class_report(conf_mat):
    tp, fp, fn, tn = conf_mat.flatten()
    measures = {}
    measures['accuracy'] = (tp + tn) / (tp + fp + fn + tn)
    measures['specificity'] = tn / (tn + fp)        # (true negative rate)
    measures['sensitivity'] = tp / (tp + fn)        # (recall, true positive rate)
    measures['precision'] = tp / (tp + fp)
    measures['f1score'] = 2*tp / (2*tp + fp + fn)
    return measuress

The code above finds several different measurement based off of the the tp,tn, fp, and fn datasets. Calucluates the 

In [0]:
def top_mean_feats(Xtr, features, grp_ids=None, min_tfidf=0.1, top_n=25):
    ''' Return the top n features that on average are most important amongst documents in rows
        indentified by indices in grp_ids. '''
    if grp_ids:
        D = Xtr[grp_ids].toarray()
    else:
        D = Xtr.toarray()

    D[D < min_tfidf] = 0
    tfidf_means = np.mean(D, axis=0)
    return top_tfidf_feats(tfidf_means, features, top_n)

In [0]:
def top_feats_in_doc(Xtr, features, row_id, top_n=25):
#''' Top tfidf features in specific document (matrix row) '''
  row = np.squeeze(Xtr[row_id].toarray())
  return top_tfidf_feats(row, features, top_n)

The above code is intended on showcasing the top 10 words used throughout the document. To show the output, you must run the code and a list will be genertated listing off the words in order from most to least.


In [18]:
data_samples[0].split()

['Well',
 "i'm",
 'not',
 'sure',
 'about',
 'the',
 'story',
 'nad',
 'it',
 'did',
 'seem',
 'biased.',
 'What',
 'I',
 'disagree',
 'with',
 'is',
 'your',
 'statement',
 'that',
 'the',
 'U.S.',
 'Media',
 'is',
 'out',
 'to',
 'ruin',
 'Israels',
 'reputation.',
 'That',
 'is',
 'rediculous.',
 'The',
 'U.S.',
 'media',
 'is',
 'the',
 'most',
 'pro-israeli',
 'media',
 'in',
 'the',
 'world.',
 'Having',
 'lived',
 'in',
 'Europe',
 'I',
 'realize',
 'that',
 'incidences',
 'such',
 'as',
 'the',
 'one',
 'described',
 'in',
 'the',
 'letter',
 'have',
 'occured.',
 'The',
 'U.S.',
 'media',
 'as',
 'a',
 'whole',
 'seem',
 'to',
 'try',
 'to',
 'ignore',
 'them.',
 'The',
 'U.S.',
 'is',
 'subsidizing',
 'Israels',
 'existance',
 'and',
 'the',
 'Europeans',
 'are',
 'not',
 '(at',
 'least',
 'not',
 'to',
 'the',
 'same',
 'degree).',
 'So',
 'I',
 'think',
 'that',
 'might',
 'be',
 'a',
 'reason',
 'they',
 'report',
 'more',
 'clearly',
 'on',
 'the',
 'atrocities.',
 'What'

In [22]:
wordlist = data_samples[0].split()
BigString = ' '.join(data_samples)
print(BiString)
wordfreq = [BigString]
for w in wordlist:
  wordfreq.append(wordlist.count(w))
str(list(zip(wordlist, wordfreq)))

Well i'm not sure about the story nad it did seem biased. What
I disagree with is your statement that the U.S. Media is out to
ruin Israels reputation. That is rediculous. The U.S. media is
the most pro-israeli media in the world. Having lived in Europe
I realize that incidences such as the one described in the
letter have occured. The U.S. media as a whole seem to try to
ignore them. The U.S. is subsidizing Israels existance and the
Europeans are not (at least not to the same degree). So I think
that might be a reason they report more clearly on the
atrocities.
	What is a shame is that in Austria, daily reports of
the inhuman acts commited by Israeli soldiers and the blessing
received from the Government makes some of the Holocaust guilt
go away. After all, look how the Jews are treating other races
when they got power. It is unfortunate.
 






Yeah, do you expect people to read the FAQ, etc. and actually accept hard
atheism?  No, you need a little leap of faith, Jimmy.  Your logic 

'[(\'Well\', \'Well i\\\'m not sure about the story nad it did seem biased. What\\nI disagree with is your statement that the U.S. Media is out to\\nruin Israels reputation. That is rediculous. The U.S. media is\\nthe most pro-israeli media in the world. Having lived in Europe\\nI realize that incidences such as the one described in the\\nletter have occured. The U.S. media as a whole seem to try to\\nignore them. The U.S. is subsidizing Israels existance and the\\nEuropeans are not (at least not to the same degree). So I think\\nthat might be a reason they report more clearly on the\\natrocities.\\n\\tWhat is a shame is that in Austria, daily reports of\\nthe inhuman acts commited by Israeli soldiers and the blessing\\nreceived from the Government makes some of the Holocaust guilt\\ngo away. After all, look how the Jews are treating other races\\nwhen they got power. It is unfortunate.\\n \\n\\n\\n\\n\\n\\n\\nYeah, do you expect people to read the FAQ, etc. and actually accept hard\\n

Above cell combings string with list because of the 'BigString' command.